In [1]:
import glob
import os
import sys
import carla
import cv2
import random
import time
import numpy as np
import math
from collections import deque
from keras.applications.xception import Xception
from keras.layers import Dense, GlobalAveragePooling2D
from keras.optimizers import Adam
from keras.models import Model
from keras.callbacks import TensorBoard
from keras.models import load_model

import tensorflow as tf
#import keras.backend.tensorflow_backend as backend
from keras.backend import set_session as backend
from threading import Thread
import datetime

from tqdm import tqdm

In [3]:
import glob
import os
import sys
import carla
import cv2
import random
import time
import numpy as np
import math
from collections import deque
import tensorflow as tf
#from tensorflow.keras.applications.xception import Xception
from tensorflow.keras.layers import Dense, GlobalAveragePooling2D
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.models import Model
from tensorflow.keras.callbacks import TensorBoard
from tensorflow.keras.models import load_model
from tensorflow.keras import backend as K
from tensorflow.keras.models import Sequential, Model
from tensorflow.keras.layers import (
    Conv2D, Activation, AveragePooling2D, Flatten, Dense, GlobalAveragePooling2D, Input
)
from tensorflow.keras.optimizers import Adam
from threading import Thread

from threading import Thread
import datetime

from tqdm import tqdm

In [4]:
SHOW_PREVIEW = False
IM_WIDTH = 640
IM_HEIGHT = 480
IMG_WIDTH = 640
IMG_HEIGHT = 480
SECONDS_PER_EPISODE = 10
REPLAY_MEMORY_SIZE = 5_000
MIN_REPLAY_MEMORY_SIZE = 1_000
MINIBATCH_SIZE = 16
PREDICTION_BATCH_SIZE = 1
TRAINING_BATCH_SIZE = MINIBATCH_SIZE // 4
UPDATE_TARGET_EVERY = 5

MODEL_NAME = "DQNFinal"
MODEL_NAMME = "DQNN"
MEMORY_FRACTION = 0.8
MIN_REWARD = 0

EPISODES = 10000

DISCOUNT = 0.99
epsilon = 1
EPSILON_DECAY = 0.95 ## 0.9975 99975
MIN_EPSILON = 0.001

AGGREGATE_STATS_EVERY = 10

# Tensorboard


In [5]:
class ModifiedTensorBoard(TensorBoard):

    # Overriding init to set initial step and writer (we want one log file for all .fit() calls)
    def __init__(self, **kwargs):
       # self.log_dir = kwargs.get('log_dir', 'logs/default')  # Utiliser une valeur par défaut si log_dir n'est pas défini
        super().__init__(**kwargs)
        self.step = 1
        self.writer = tf.summary.create_file_writer(self.log_dir)
        self._log_write_dir = os.path.join(self.log_dir, MODEL_NAME)
        

    # Overriding this method to stop creating default log writer
    def set_model(self, model):
        self.model = model

        self._train_dir = os.path.join(self._log_write_dir, 'train')
        self._train_step = self.model._train_counter

        self._val_dir = os.path.join(self._log_write_dir, 'validation')
        self._val_step = self.model._test_counter

        self._should_write_train_graph = False

    # Overrided, saves logs with our step number
    # (otherwise every .fit() will start writing from 0th step)
    def on_epoch_end(self, epoch, logs=None):
        print("&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end")
        self.update_stats(**logs)
        #with self.writer.as_default():
         #   for key, value in logs.items():
          #      tf.summary.scalar(key,value,step=self.step)
        #self.writer.flush()
        #self.step +=1
        #self.update_stats(**logs)

    # Overrided
    # We train for one batch only, no need to save anything at epoch end
    def on_batch_end(self, batch, logs=None):
        pass

    # Overrided, so won't close writer
    def on_train_end(self, _):
        pass

    # Custom method for saving own metrics
    # Creates writer, writes custom metrics and closes writer
    def update_stats(self, **stats):
        self._write_logs(stats, self.step)
        
    def _write_logs(self, logs, index):
        with self.writer.as_default():
            for name, value in logs.items():
                tf.summary.scalar(name, value, step=index)
                self.step += 1
                self.writer.flush()    
       # print("logging stats :",stats)
       # with self.writer.as_default():
        #    for key, value in stats.items():
         #       tf.summary.scalar(key, value, step=self.step)
       # self.writer.flush()
       # self.step += 1
        #self._write_logs(stats, self.step)


# car env 

In [6]:


class CarEnv:
    SHOW_CAM = SHOW_PREVIEW
    STEER_AMT = 0.3

    im_width = IM_WIDTH
    im_height = IM_HEIGHT
    actor_list = []

    front_camera = None
    collision_hist = []

    def __init__(self):
        self.client = carla.Client('localhost', 2000)
        self.client.set_timeout(5.0)

        # Once we have a client we can retrieve the world that is currently
        # running.
        self.world = self.client.get_world()

        # The world contains the list blueprints that we can use for adding new
        # actors into the simulation.
        self.blueprint_library = self.world.get_blueprint_library()

        # Now let's filter all the blueprints of type 'vehicle' and choose one
        # at random.
        #print(blueprint_library.filter('vehicle'))
        self.model_3 = self.blueprint_library.filter('model3')[0]
        self.map = self.world.get_map()
        
    def is_collision_free(location):
    # Cast a ray towards the ground to detect any potential collision
        ray = carla.Raycast(location, carla.Vector3D(0, 0, -1))  # Ray pointing downward
        return ray.distance > 0.5   
   

    def reset(self):
        self.collision_hist = []
        self.actor_list = []

        self.transform = random.choice(self.world.get_map().get_spawn_points())
        self.vehicle = self.world.try_spawn_actor(self.model_3, self.transform)
        self.actor_list.append(self.vehicle)
        
        
                
        self.rgb_cam = self.world.get_blueprint_library().find('sensor.camera.rgb')
        self.rgb_cam.set_attribute('image_size_x', f'{self.im_width}')
        self.rgb_cam.set_attribute('image_size_y', f'{self.im_height}')
        self.rgb_cam.set_attribute('fov', '110')


        transform = carla.Transform(carla.Location(x=2.5, z=0.7))

        self.sensor = self.world.spawn_actor(self.rgb_cam, transform, attach_to=self.vehicle)

        self.actor_list.append(self.sensor)
        self.sensor.listen(lambda data: self.process_img(data))

        self.vehicle.apply_control(carla.VehicleControl(throttle=0.0, brake=0.0))

        time.sleep(4) # sleep to get things started and to not detect a collision when the car spawns/falls from sky.


        while self.front_camera is None:
            time.sleep(0.01)

        self.episode_start = time.time()

        self.vehicle.apply_control(carla.VehicleControl(brake=0.0, throttle=0.0))

        return self.front_camera
    
    def sur_la_route(self):
        vehicle_location = self.vehicle.get_location()
        waypoint = self.map.get_waypoint(vehicle_location, project_to_road=True, lane_type=carla.LaneType.Driving)
        distance_to_center = vehicle_location.distance(waypoint.transform.location)

        lane_width = waypoint.lane_width

        max_distance = lane_width / 2

        normalized_distance = min(distance_to_center / max_distance, 1.0)
        reward = np.exp(-normalized_distance)
        
        if distance_to_center < max_distance:
    # Le véhicule est sur la route
            return True , reward
        else:
    # Le véhicule est hors de la route
           return False , reward

    def collision_data(self, event):
        self.collision_hist.append(event)

    def process_img(self, image):
        i = np.array(image.raw_data)
        #np.save("iout.npy", i)
        i2 = i.reshape((self.im_height, self.im_width, 4))
        i3 = i2[:, :, :3]
        if self.SHOW_CAM:
            cv2.imshow("",i3)
            cv2.waitKey(1)
        self.front_camera = i3

    def step(self, action):
        #print("step")
        '''
        For now let's just pass steer left, center, right?
        0, 1, 2
        '''
        if action == 0:
            self.vehicle.apply_control(carla.VehicleControl(throttle=1.0, steer=0))
        elif action == 1:
            self.vehicle.apply_control(carla.VehicleControl(throttle=1.0, steer=-1*self.STEER_AMT))
        elif action == 2:
            self.vehicle.apply_control(carla.VehicleControl(throttle=1.0, steer=1*self.STEER_AMT))

        v = self.vehicle.get_velocity()
        kmh = int(3.6 * math.sqrt(v.x**2 + v.y**2 + v.z**2))
        
        on_road, reward = self.sur_la_route()
        done= False
        #print("reward ", reward )
        if len(self.collision_hist) != 0:
            done = True
            reward = -1
            #print("Episode terminé par collision.")
        elif  not on_road:
            reward -= 1
        elif kmh < 50:
            reward -= 0.5 
        
        #print("print ", reward)
       
        if self.episode_start + SECONDS_PER_EPISODE < time.time():
            done = True
            #print("Episode terminé par dépassement de temps.")
        #print("--------------------------------fin step ")
        return self.front_camera, reward, done, None

# DQN Agent

In [7]:

def model_base_64x3_CNN(input_shape):
    model = Sequential()

    model.add(Conv2D(64, (3, 3), input_shape=input_shape, padding='same'))
    model.add(Activation('relu'))
    model.add(AveragePooling2D(pool_size=(5, 5), strides=(3, 3), padding='same'))

    model.add(Conv2D(64, (3, 3), padding='same'))
    model.add(Activation('relu'))
    model.add(AveragePooling2D(pool_size=(5, 5), strides=(3, 3), padding='same'))

    model.add(Conv2D(64, (3, 3), padding='same'))
    model.add(Activation('relu'))
    model.add(AveragePooling2D(pool_size=(5, 5), strides=(3, 3), padding='same'))

    model.add(Flatten())

    return model.input, model.output

class DQNAgent:
    def __init__(self):
        self.model = self.create_model()
        self.target_model = self.create_model()
        self.target_model.set_weights(self.model.get_weights())
        #we train from randomly selected data from our replay memory
        self.replay_memory = deque(maxlen=REPLAY_MEMORY_SIZE)
        
        self.log_dir = f".logs/{MODEL_NAME}-{int(time.time())}"

        self.tensorboard = ModifiedTensorBoard(log_dir=self.log_dir)
        #self.tensorboard = tf.keras.callbacks.TensorBoard(log_dir=self.log_dir, histogram_freq=1)
        #self.custom_callback = CustomCallback(self.log_dir)

        
        #self.log_dir = "logs/fit/" + datetime.datetime.now().strftime("%Y%m%d-%H%M%S")
        # will track when it's time to update the target model
        self.target_update_counter = 0
        #self.graph = tf.get_default_graph()

        self.terminate = False
        self.last_logged_episode = 0
        self.training_initialized = False # waiting for TF to get rolling

    def create_model(self):
        #base_model = Xception(weights=None, include_top=False, input_shape=(IM_HEIGHT, IM_WIDTH,3))
        input_shape = (IM_HEIGHT, IM_WIDTH, 3)
        # Récupérer l'entrée et les sorties intermédiaires du modèle personnalisé
        inputs, x = model_base_64x3_CNN(input_shape)

        
        #x = base_model.output
        #x = GlobalAveragePooling2D()(x)

        predictions = Dense(3, activation="linear")(x)
        model = Model(inputs=inputs, outputs=predictions)
        model.compile(loss="mse", optimizer=Adam(learning_rate=0.001), metrics=["accuracy"])
        return model

    def update_replay_memory(self, transition):
        #print("update transaction",len(self.replay_memory))
        #print(f"Transition ajoutée : {transition}")
        # transition = (current_state, action, reward, new_state, done)
        self.replay_memory.append(transition)

    def train(self):
#print(f"Nombre d'éléments dans la mémoire de replay: {len(self.replay_memory)}")

        if len(self.replay_memory) < MIN_REPLAY_MEMORY_SIZE:
            #print("Pas assez de données dans la mémoire de replay.")
            return
       # print(" ----------------------------------------------------------------------------apres if train  ")
       # print(f"Nombre d'éléments dans la mémoire de replay: {len(self.replay_memory)}")

        minibatch = random.sample(self.replay_memory, MINIBATCH_SIZE)

        current_states = np.array([transition[0] for transition in minibatch])/255
        #with self.graph.as_default():
        current_qs_list = self.model.predict(current_states, PREDICTION_BATCH_SIZE)

        new_current_states = np.array([transition[3] for transition in minibatch])/255
        #with self.graph.as_default():
        future_qs_list = self.target_model.predict(new_current_states, PREDICTION_BATCH_SIZE)

        X = []
        y = []

        for index, (current_state, action, reward, new_state, done) in enumerate(minibatch):
            if not done:
                max_future_q = np.max(future_qs_list[index])
                new_q = reward + DISCOUNT * max_future_q
            else:
                new_q = reward

            current_qs = current_qs_list[index]
            current_qs[action] = new_q

            X.append(current_state)
            y.append(current_qs)

        log_this_step = False
        if self.tensorboard.step > self.last_logged_episode:
            log_this_step = True
            self.last_log_episode = self.tensorboard.step

        #with self.graph.as_default():
        
        #tensorboard_callback = tf.keras.callbacks.TensorBoard(log_dir=log_dir, histogram_freq=1)
        self.model.fit(np.array(X)/255, np.array(y), batch_size=TRAINING_BATCH_SIZE, verbose=0, shuffle=False, callbacks=[self.tensorboard] if log_this_step else None)


        if log_this_step:
            self.target_update_counter += 1

        if self.target_update_counter > UPDATE_TARGET_EVERY:
            self.target_model.set_weights(self.model.get_weights())
            self.target_update_counter = 0

    def get_qs(self, state):
        return self.model.predict(np.array(state).reshape(-1, *state.shape)/255)[0]

    def train_in_loop(self):
        #print("Initialisation de l'entraînement")
        X = np.random.uniform(size=(1, IM_HEIGHT, IM_WIDTH, 3)).astype(np.float32)
        y = np.random.uniform(size=(1, 3)).astype(np.float32)
        #with self.graph.as_default():
        self.model.fit(X,y, verbose=False, batch_size=1)

        self.training_initialized = True
       # print("Entraînement initialisé.--------------------- boocle while ")

        while True:
            if self.terminate:
            #  print("Entraînement terminé.-------------------- boucle while",len(self.replay_memory))
                return
            self.train()
            time.sleep(0.02)

# Main




In [ ]:
if __name__ == '__main__':
    FPS = 60
    # For stats
    ep_rewards = [-1]

    # For more repetitive results
    random.seed(1)
    np.random.seed(1)
    #tf.set_random_seed(seed)
    tf.random.set_seed(1)
    
    # Memory fraction, used mostly when trai8ning multiple agents
    #Configuration GPU dans tanserflow 2.x
    gpus=tf.config.list_physical_devices('GPU')
    if gpus:
        try:
            for gpu in gpus:
                tf.config.experimental.set_virtual_device_configuration(
                gpu,
                [tf.config.experimental.VirtualDeviceConfiguration(memory_limit=MEMORY_FRACTION*1024*8)]
                )
            print("configration GPU reussie ")
        except RuntimeError as e:
            print(f"Erreur lors de configuration des GPU :{e}" )
            
   # gpu_options = tf.GPUOptions(per_process_gpu_memory_fraction=MEMORY_FRACTION)
   #backend.set_session(tf.Session(config=tf.ConfigProto(gpu_options=gpu_options)))

    # Create models folder
    if not os.path.isdir('models'):
        os.makedirs('models')

    # Create agent and environment
    agent = DQNAgent()
    env = CarEnv()
    
    

    # Start training thread and wait for training to be initialized
    trainer_thread = Thread(target=agent.train_in_loop, daemon=True)
    trainer_thread.start()
    
    while not agent.training_initialized:
        time.sleep(0.02)
    # Initialize predictions - forst prediction takes longer as of initialization that has to be done
    # It's better to do a first prediction then before we start iterating over episode steps
    agent.get_qs(np.ones((env.im_height, env.im_width, 3)))
#    print("////////////////////////////////////////////avant epispdes")

    # Iterate over episodes
    for episode in tqdm(range(1, EPISODES + 1), ascii=True, unit='episodes'):
       # print("episode")
        env.collision_hist = []
        # Update tensorboard step every episode
        agent.tensorboard.step = episode

            # Restarting episode - reset episode reward and step number
        episode_reward = 0
        step = 1

            # Reset environment and get initial state
        current_state = env.reset()

            # Reset flag and start iterating until episode ends
        done = False
        episode_start = time.time()

            # Play for given number of seconds only
        while True:
           # print("Play for given number of seconds only")
                # This part stays mostly the same, the change is to query a model for Q values
            if np.random.random() > epsilon:
                    # Get action from Q table
                action = np.argmax(agent.get_qs(current_state))
            else:
                # Get random action
                action = np.random.randint(0, 3)
                # This takes no time, so we add a delay matching 60 FPS (prediction above takes longer)
                time.sleep(1/FPS)
           # print("**************************************************")
            new_state, reward, done, _ = env.step(action)
                # Transform new continous state to new discrete state and count reward
            episode_reward += reward
#print(f" action: {action}, reward: {reward}, new_state: {new_state}, done: {done}")

                # Every step we update replay memory
            agent.update_replay_memory((current_state, action, reward, new_state, done))

            current_state = new_state
            # Show current frame
            #cv2.imshow(f'Agent - preview', current_state)
            #cv2.waitKey(1)
            step += 1

            if done:
                break

            # End of episode - destroy agents
        for actor in env.actor_list:
            actor.destroy()

            # Append episode reward to a list and log stats (every given number of episodes)
        ep_rewards.append(episode_reward)
        if not episode % AGGREGATE_STATS_EVERY or episode == 1:
            average_reward = sum(ep_rewards[-AGGREGATE_STATS_EVERY:])/len(ep_rewards[-AGGREGATE_STATS_EVERY:])
            min_reward = min(ep_rewards[-AGGREGATE_STATS_EVERY:])
            max_reward = max(ep_rewards[-AGGREGATE_STATS_EVERY:])
            agent.tensorboard.update_stats(reward_avg=average_reward, reward_min=min_reward, reward_max=max_reward, epsilon=epsilon)

                # Save model, but only when min reward is greater or equal a set value
            if min_reward >= MIN_REWARD:
                #agent.model.save(f'models/{MODEL_NAME}__{max_reward:_>7.2f}max_{average_reward:_>7.2f}avg_{min_reward:_>7.2f}min__{int(time.time())}.model')
                agent.model.save(f'models/{MODEL_NAME}__{max_reward:_>7.2f}max_{average_reward:_>7.2f}avg_{min_reward:_>7.2f}min__{int(time.time())}.h5',save_format='h5'
                )
        # Decay epsilon
        if epsilon > MIN_EPSILON:
            epsilon *= EPSILON_DECAY
            epsilon = max(MIN_EPSILON, epsilon)


    # Set termination flag for training thread and wait for it to finish
    agent.terminate = True
    trainer_thread.join()
    agent.model.save(f'models/{MODEL_NAME}__{max_reward:_>7.2f}max_{average_reward:_>7.2f}avg_{min_reward:_>7.2f}min__{int(time.time())}.model')

configration GPU reussie 
1/1 [==============================] - 0s 98ms/step


  0%|                                                                                  | 0/10000 [00:00<?, ?episodes/s]

1/1 [==============================] - 0s 33ms/step


  0%|                                                                       | 1/10000 [00:11<31:13:00, 11.24s/episodes]

1/1 [==============================] - 0s 32ms/step


...

16/16 [==============================] - 1s 73ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
16/16 [==============================] - 1s 60ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
14/16 [=========================>....] - ETA: 0s

 20%|#############2                                                    | 2014/10000 [5:49:23<19:45:00,  8.90s/episodes]

16/16 [==============================] - 2s 104ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
16/16 [==============================] - 1s 62ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
1/1 [==============================] - 0s 143ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
1/1 [==============================] - 0s 218ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
1/1 [==============================] - 0s 108ms/step


 20%|#############2                                                    | 2015/10000 [5:49:37<23:09:04, 10.44s/episodes]

16/16 [==============================] - 1s 80ms/step


In [ ]:
if __name__ == '__main__':
    FPS = 60
    # For stats
    ep_rewards = [-200]

    # For more repetitive results
    random.seed(1)
    np.random.seed(1)
    #tf.set_random_seed(seed)
    tf.random.set_seed(1)
    
    # Memory fraction, used mostly when trai8ning multiple agents
    #Configuration GPU dans tanserflow 2.x
    gpus=tf.config.list_physical_devices('GPU')
    if gpus:
        try:
            for gpu in gpus:
                tf.config.experimental.set_virtual_device_configuration(
                gpu,
                [tf.config.experimental.VirtualDeviceConfiguration(memory_limit=MEMORY_FRACTION*1024*8)]
                )
            print("configration GPU reussie ")
        except RuntimeError as e:
            print(f"Erreur lors de configuration des GPU :{e}" )
            
   # gpu_options = tf.GPUOptions(per_process_gpu_memory_fraction=MEMORY_FRACTION)
   #backend.set_session(tf.Session(config=tf.ConfigProto(gpu_options=gpu_options)))

    # Create models folder
    if not os.path.isdir('models'):
        os.makedirs('models')

    # Create agent and environment
    agent = DQNAgent()
    env = CarEnv()

16/16 [==============================] - 0s 5ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
16/16 [==============================] - 0s 5ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
16/16 [==============================] - 0s 6ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
16/16 [==============================] - 0s 5ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
16/16 [==============================] - 0s 5ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
16/16 [==============================] - 0s 6ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
16/16 [==============================] - 0s 5ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
16/16 [==============================] - 0s 6ms/step
&&&&&&&&&

16/16 [==============================] - 0s 6ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
16/16 [==============================] - 0s 7ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
16/16 [==============================] - 0s 6ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
16/16 [==============================] - 0s 6ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
16/16 [==============================] - 0s 6ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
16/16 [==============================] - 0s 6ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
16/16 [==============================] - 0s 5ms/step
&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&&on_epoch_end
16/16 [==============================] - 0s 6ms/step
&&&&&&&&&

In [ ]:


MODEL_PATH = 'models/Xception____17.00max__-37.20avg__-53.00min__1735218545.model'

if __name__ == '__main__':

    # Memory fraction
    #gpu_options = tf.GPUOptions(per_process_gpu_memory_fraction=MEMORY_FRACTION)
    #backend.set_session(tf.Session(config=tf.ConfigProto(gpu_options=gpu_options)))
    gpus=tf.config.list_physical_devices('GPU')
    if gpus:
        try:
            for gpu in gpus:
                tf.config.experimental.set_virtual_device_configuration(
                gpu,
                [tf.config.experimental.VirtualDeviceConfiguration(memory_limit=MEMORY_FRACTION*1024*8)]
                )
            print("configration GPU reussie ")
        except RuntimeError as e:
            print(f"Erreur lors de configuration des GPU :{e}" )
            
    # Load the model
    model = load_model(MODEL_PATH)

    # Create environment
    env = CarEnv()

    # For agent speed measurements - keeps last 60 frametimes
    fps_counter = deque(maxlen=60)

    # Initialize predictions - first prediction takes longer as of initialization that has to be done
    # It's better to do a first prediction then before we start iterating over episode steps
    model.predict(np.ones((1, env.im_height, env.im_width, 3)))

    # Loop over episodes
    while True:

        print('Restarting episode')

        # Reset environment and get initial state
        current_state = env.reset()
        env.collision_hist = []

        done = False

        # Loop over steps
        while True:

            # For FPS counter
            step_start = time.time()

            # Show current frame
            cv2.imshow(f'Agent - preview', current_state)
            cv2.waitKey(1)

            # Predict an action based on current observation space
            qs = model.predict(np.array(current_state).reshape(-1, *current_state.shape)/255)[0]
            action = np.argmax(qs)

            # Step environment (additional flag informs environment to not break an episode by time limit)
            new_state, reward, done, _ = env.step(action)

            # Set current step for next loop iteration
            current_state = new_state

            # If done - agent crashed, break an episode
            if done:
                break

            # Measure step time, append to a deque, then print mean FPS for last 60 frames, q values and taken action
            frame_time = time.time() - step_start
            fps_counter.append(frame_time)
            print(f'Agent: {len(fps_counter)/sum(fps_counter):>4.1f} FPS | Action: [{qs[0]:>5.2f}, {qs[1]:>5.2f}, {qs[2]:>5.2f}] {action}')

        # Destroy an actor at end of episode
        for actor in env.actor_list:
            actor.destroy()

configration GPU reussie 
1/1 [==============================] - 27s 27s/step
Restarting episode
1/1 [==============================] - 0s 63ms/step
Agent:  4.5 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 62ms/step
Agent:  5.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 63ms/step
Agent:  5.1 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 59ms/step
Agent:  5.2 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 64ms/step
Agent:  5.3 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 64ms/step
Agent:  5.3 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 64ms/step
Agent:  5.3 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 59ms/step
Agent:  5.3 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 59ms/step
Agent:  5.3 FPS | Action: [ 0.02,  

1/1 [==============================] - 0s 41ms/step
Agent:  8.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 48ms/step
Agent:  7.9 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 50ms/step
Agent:  7.9 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 46ms/step
Agent:  7.9 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 38ms/step
Agent:  7.8 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 41ms/step
Agent:  7.8 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 37ms/step
Agent:  7.8 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 40ms/step
Agent:  7.8 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 42ms/step
Agent:  7.8 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 41ms/step
Agent:  7.8 FPS | Action: [ 0.

1/1 [==============================] - 0s 31ms/step
Agent:  8.6 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 31ms/step
Agent:  8.6 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 28ms/step
Agent:  8.6 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 30ms/step
Agent:  8.6 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 30ms/step
Agent:  8.6 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 27ms/step
Agent:  8.7 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 30ms/step
Agent:  8.7 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 31ms/step
Agent:  8.7 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 29ms/step
Agent:  8.7 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 29ms/step
Agent:  8.7 FPS | Action: [ 0.

1/1 [==============================] - 0s 33ms/step
Agent: 10.2 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 34ms/step
Agent: 10.1 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 36ms/step
Agent: 10.1 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 33ms/step
Agent: 10.1 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 35ms/step
Agent: 10.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 34ms/step
Agent: 10.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 34ms/step
Agent: 10.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 33ms/step
Agent: 10.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 34ms/step
Agent: 10.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 36ms/step
Agent: 10.0 FPS | Action: [ 0.

1/1 [==============================] - 0s 29ms/step
Agent:  9.6 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 33ms/step
Agent:  9.6 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 30ms/step
Agent:  9.6 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 31ms/step
Agent:  9.6 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 29ms/step
Agent:  9.6 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 29ms/step
Agent:  9.6 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 30ms/step
Agent:  9.7 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 30ms/step
Agent:  9.7 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 27ms/step
Agent:  9.7 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 28ms/step
Agent:  9.8 FPS | Action: [ 0.

...

1/1 [==============================] - 0s 75ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 94ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 136ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 64ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 80ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 63ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 74ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 166ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 110ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 62ms/step
Agent:  2.0 FPS | Action: [

1/1 [==============================] - 0s 113ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 61ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 65ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 148ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 60ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 81ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 71ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 65ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 54ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 144ms/step
Agent:  2.0 FPS | Action: [

1/1 [==============================] - 0s 145ms/step
Agent:  1.8 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 61ms/step
Agent:  1.8 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 62ms/step
Agent:  1.9 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 63ms/step
Agent:  1.9 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 71ms/step
Agent:  1.9 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 148ms/step
Restarting episode
1/1 [==============================] - 0s 60ms/step
Agent:  1.9 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 245ms/step
Agent:  1.9 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 64ms/step
Agent:  1.9 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 100ms/step
Agent:  1.9 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==

1/1 [==============================] - 0s 65ms/step
Agent:  2.1 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 152ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 70ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 48ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 223ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 61ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 75ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 77ms/step
Restarting episode
1/1 [==============================] - 0s 80ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 60ms/step
Agent:  2.0 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [====

1/1 [==============================] - 0s 61ms/step
Agent:  1.9 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 90ms/step
Agent:  1.9 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 90ms/step
Agent:  1.9 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 61ms/step
Restarting episode
1/1 [==============================] - 0s 72ms/step
Agent:  1.9 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 60ms/step
Agent:  1.8 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 61ms/step
Agent:  1.8 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 70ms/step
Agent:  1.9 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 196ms/step
Agent:  1.9 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [==============================] - 0s 218ms/step
Agent:  1.8 FPS | Action: [ 0.02,  0.01,  0.02] 0
1/1 [====